In [11]:
import sys
import re
import requests
import pprint
import json
import datetime
from pytz import timezone
from bs4 import BeautifulSoup
from multiprocessing import Pool

import pandas as pd
import numpy as np
from tqdm import tqdm
import matplotlib.pyplot as plt
import seaborn as sns
import warnings

warnings.filterwarnings('ignore')
pd.set_option('display.max_rows', 100)

In [12]:
def get_game_id(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.text, 'lxml')
    for tag in soup.find_all(class_=['top-level-genre', "list top-level-subgenres", "list column first"]):
        tag.decompose()
    r = soup.find_all(class_='column')
    game_ids = [x.strip('/id"') for x in re.findall('/id\d*"', str(r))]
    return game_ids

In [13]:
def write_json_file(sub_genre_id, letter, page, game_id):
#     path = 'input/test.json'
#     path = 'input/app_all_info.json'
    url = 'https://itunes.apple.com/lookup?'
    params = {'country': 'JP', 'id': game_id}

    r = requests.get(url, params=params)
    request_datetime = get_request_datetime(r)
    json_data = r.json()
    json_data.update({'sub_genre_id': sub_genre_id})
    json_data.update({'letter': letter})
    json_data.update({'page': page})
    json_data.update({'id': game_id})
    json_data.update({'request_at': request_datetime})
    append_json_to_file(json_data, path)
    return 'Success'

In [14]:
def get_request_datetime(r):
    request_datetime = r.headers['Date']
    request_datetime = datetime.datetime.strptime(request_datetime, '%a, %d %b %Y %X %Z')
    request_datetime = request_datetime.astimezone(timezone('Asia/Tokyo'))
    request_datetime = request_datetime.isoformat()
    return request_datetime

In [15]:
def append_json_to_file(data: dict, path_file: str) -> bool:
    with open(path_file, 'ab+') as f:
        f.seek(0,2)
        if f.tell() == 0 :
            f.write(json.dumps([data]).encode())
        else :
            f.seek(-1,2)
            f.truncate()
            f.write(' , '.encode())
            f.write(json.dumps(data).encode())
            f.write(']'.encode())
    return f.close()

In [16]:
url_parent = 'https://apps.apple.com/jp/genre/id{}?letter={}&page={}#page'
sub_genre_id_dict = {
    'アクション': 7001,
    'アドベンチャー': 7002,
    'ボード': 7004,
    'カード': 7005,
    'カジノ': 7006,
   'カジュアル': 7003,
    'さいころ': 7007,
    '教育': 7008,
    'ファミリー': 7009,
    'ミュージック': 7011,
    'パズル': 7012,
    'レーシング': 7013,
    'ロールプレイング': 7014,
    'シミュレーション': 7015,
    'スポーツ': 7016,
    'ストラテジー': 7017,
    'トリビア': 7018,
    '単語': 7019
}
letters = [chr(i) for i in range(65, 65+26)]
letters.append('#')
pages = range(1, 100)

In [17]:
# df = pd.read_json('input/app_all_info.json')
# df

In [18]:
# gotten_game_ids = list(df['id'].values)
# gotten_game_ids = [str(id) for id in gotten_game_ids]
# gotten_game_ids

In [10]:
# len(gotten_game_ids)

283383

In [11]:
# import gc
# del df
# gc.collect()

0

#### single process

In [20]:
%%time
i = 0
game_id = 0
gotten_game_ids = []
get_game_id_error = []
write_json_file_error = []

for sub_genre_id in sub_genre_id_dict.values():
    for letter in letters:
        for page in pages:
            url = url_parent.format(sub_genre_id, letter, page)
            try:
                game_ids = get_game_id(url)
            except:
                get_game_id_error.append([sub_genre_id, letter, page])
                print('get_game_id_error')
                print(sub_genre_id, letter, page)
                break
            if len(game_ids) == 0:
                get_game_id_error.append([sub_genre_id, letter, page])
                print('len(game_ids) == 0')
                print(sub_genre_id, letter, page)
                break
            for game_id in game_ids:
                if game_id in gotten_game_ids:
                    print('game_id in gotten_game_ids')
                    print(sub_genre_id, letter, page, game_id)
                else:
                    gotten_game_ids.append(game_id)
                    i += 1
                    if i%1000 == 0:
                        print('*'*30+str(i))
                    try:
                        write_json_file(sub_genre_id, letter, page, game_id)
                    except:
                        write_json_file_error.append([sub_genre_id, letter, page, game_id])
                        print('write_json_file_error')
                        print(sub_genre_id, letter, page, game_id)

len(game_ids) == 0
7007 A 1
len(game_ids) == 0
7007 B 1
len(game_ids) == 0
7007 C 1
len(game_ids) == 0
7007 D 1
len(game_ids) == 0
7007 E 1
len(game_ids) == 0
7007 F 1
len(game_ids) == 0
7007 G 1
len(game_ids) == 0
7007 H 1
len(game_ids) == 0
7007 I 1
len(game_ids) == 0
7007 J 1
len(game_ids) == 0
7007 K 1
len(game_ids) == 0
7007 L 1
len(game_ids) == 0
7007 M 1
len(game_ids) == 0
7007 N 1
len(game_ids) == 0
7007 O 1
len(game_ids) == 0
7007 P 1
len(game_ids) == 0
7007 Q 1
len(game_ids) == 0
7007 R 1
len(game_ids) == 0
7007 S 1
len(game_ids) == 0
7007 T 1
len(game_ids) == 0
7007 U 1
len(game_ids) == 0
7007 V 1
len(game_ids) == 0
7007 W 1
len(game_ids) == 0
7007 X 1
len(game_ids) == 0
7007 Y 1
len(game_ids) == 0
7007 Z 1
len(game_ids) == 0
7007 # 1
len(game_ids) == 0
7008 A 1
len(game_ids) == 0
7008 B 1
len(game_ids) == 0
7008 C 1
len(game_ids) == 0
7008 D 1
len(game_ids) == 0
7008 E 1
len(game_ids) == 0
7008 F 1
len(game_ids) == 0
7008 G 1
len(game_ids) == 0
7008 H 1
len(game_ids) == 0
7

game_id in gotten_game_ids
7009 C 14 931209006
game_id in gotten_game_ids
7009 C 19 929123965
game_id in gotten_game_ids
7009 C 19 1093360066
******************************8000
game_id in gotten_game_ids
7009 C 21 582655834
game_id in gotten_game_ids
7009 C 23 1086515449
game_id in gotten_game_ids
7009 C 24 1300936234
game_id in gotten_game_ids
7009 C 24 1489769659
game_id in gotten_game_ids
7009 C 25 1203367423
game_id in gotten_game_ids
7009 C 25 1183688629
game_id in gotten_game_ids
7009 C 26 1214688059
game_id in gotten_game_ids
7009 C 27 1114411377
game_id in gotten_game_ids
7009 C 27 1080708155
******************************9000
game_id in gotten_game_ids
7009 C 29 1131528562
game_id in gotten_game_ids
7009 C 29 1003165329
game_id in gotten_game_ids
7009 C 30 953085373
game_id in gotten_game_ids
7009 C 30 1001929438
game_id in gotten_game_ids
7009 C 32 819072539
len(game_ids) == 0
7009 C 35
game_id in gotten_game_ids
7009 D 1 796785243
******************************10000
game_id 

game_id in gotten_game_ids
7009 E 55 1210613650
game_id in gotten_game_ids
7009 E 56 1210613650
game_id in gotten_game_ids
7009 E 57 1210613650
game_id in gotten_game_ids
7009 E 58 1210613650
game_id in gotten_game_ids
7009 E 59 1210613650
game_id in gotten_game_ids
7009 E 60 1210613650
game_id in gotten_game_ids
7009 E 61 1210613650
game_id in gotten_game_ids
7009 E 62 1210613650
game_id in gotten_game_ids
7009 E 63 1210613650
game_id in gotten_game_ids
7009 E 64 1210613650
game_id in gotten_game_ids
7009 E 65 1210613650
game_id in gotten_game_ids
7009 E 66 1210613650
game_id in gotten_game_ids
7009 E 67 1210613650
game_id in gotten_game_ids
7009 E 68 1210613650
game_id in gotten_game_ids
7009 E 69 1210613650
game_id in gotten_game_ids
7009 E 70 1210613650
game_id in gotten_game_ids
7009 E 71 1210613650
game_id in gotten_game_ids
7009 E 72 1210613650
game_id in gotten_game_ids
7009 E 73 1210613650
game_id in gotten_game_ids
7009 E 74 1210613650
game_id in gotten_game_ids
7009 E 75 121

game_id in gotten_game_ids
7009 H 89 1258229999
game_id in gotten_game_ids
7009 H 90 1258229999
game_id in gotten_game_ids
7009 H 91 1258229999
game_id in gotten_game_ids
7009 H 92 1258229999
game_id in gotten_game_ids
7009 H 93 1258229999
game_id in gotten_game_ids
7009 H 94 1258229999
game_id in gotten_game_ids
7009 H 95 1258229999
game_id in gotten_game_ids
7009 H 96 1258229999
game_id in gotten_game_ids
7009 H 97 1258229999
game_id in gotten_game_ids
7009 H 98 1258229999
game_id in gotten_game_ids
7009 H 99 1258229999
game_id in gotten_game_ids
7009 I 1 1062664939
game_id in gotten_game_ids
7009 I 1 736630944
game_id in gotten_game_ids
7009 I 2 839508603
game_id in gotten_game_ids
7009 I 3 599306697
game_id in gotten_game_ids
7009 I 3 1139668143
game_id in gotten_game_ids
7009 I 4 880507558
game_id in gotten_game_ids
7009 I 4 1450724443
game_id in gotten_game_ids
7009 I 5 1510564879
game_id in gotten_game_ids
7009 I 5 1445979517
game_id in gotten_game_ids
7009 I 7 1500555908
game_i

game_id in gotten_game_ids
7009 K 54 852832124
game_id in gotten_game_ids
7009 K 55 852832124
game_id in gotten_game_ids
7009 K 56 852832124
game_id in gotten_game_ids
7009 K 57 852832124
game_id in gotten_game_ids
7009 K 58 852832124
game_id in gotten_game_ids
7009 K 59 852832124
game_id in gotten_game_ids
7009 K 60 852832124
game_id in gotten_game_ids
7009 K 61 852832124
game_id in gotten_game_ids
7009 K 62 852832124
game_id in gotten_game_ids
7009 K 63 852832124
game_id in gotten_game_ids
7009 K 64 852832124
game_id in gotten_game_ids
7009 K 65 852832124
game_id in gotten_game_ids
7009 K 66 852832124
game_id in gotten_game_ids
7009 K 67 852832124
game_id in gotten_game_ids
7009 K 68 852832124
game_id in gotten_game_ids
7009 K 69 852832124
game_id in gotten_game_ids
7009 K 70 852832124
game_id in gotten_game_ids
7009 K 71 852832124
game_id in gotten_game_ids
7009 K 72 852832124
game_id in gotten_game_ids
7009 K 73 852832124
game_id in gotten_game_ids
7009 K 74 852832124
game_id in go

...

game_id in gotten_game_ids
7013 # 95 1495506021
game_id in gotten_game_ids
7013 # 95 1095227160
game_id in gotten_game_ids
7013 # 95 1113531634
game_id in gotten_game_ids
7013 # 95 1354874613
game_id in gotten_game_ids
7013 # 95 1480928437
game_id in gotten_game_ids
7013 # 95 1202690718
game_id in gotten_game_ids
7013 # 95 1261474645
game_id in gotten_game_ids
7013 # 95 1071049120
game_id in gotten_game_ids
7013 # 95 1033601528
game_id in gotten_game_ids
7013 # 95 1293634699
game_id in gotten_game_ids
7013 # 95 638809734
game_id in gotten_game_ids
7013 # 95 638290589
game_id in gotten_game_ids
7013 # 95 1144395230
game_id in gotten_game_ids
7013 # 95 1507663490
game_id in gotten_game_ids
7013 # 95 722000616
game_id in gotten_game_ids
7013 # 95 739117893
game_id in gotten_game_ids
7013 # 95 1355584120
game_id in gotten_game_ids
7013 # 95 1446635457
game_id in gotten_game_ids
7013 # 95 1153421952
game_id in gotten_game_ids
7013 # 95 423911805
game_id in gotten_game_ids
7013 # 95 14742211

game_id in gotten_game_ids
7013 # 96 920775822
game_id in gotten_game_ids
7013 # 96 1495033384
game_id in gotten_game_ids
7013 # 96 1095676682
game_id in gotten_game_ids
7013 # 96 1365265774
game_id in gotten_game_ids
7013 # 96 1495506021
game_id in gotten_game_ids
7013 # 96 1095227160
game_id in gotten_game_ids
7013 # 96 1113531634
game_id in gotten_game_ids
7013 # 96 1354874613
game_id in gotten_game_ids
7013 # 96 1480928437
game_id in gotten_game_ids
7013 # 96 1202690718
game_id in gotten_game_ids
7013 # 96 1261474645
game_id in gotten_game_ids
7013 # 96 1071049120
game_id in gotten_game_ids
7013 # 96 1033601528
game_id in gotten_game_ids
7013 # 96 1293634699
game_id in gotten_game_ids
7013 # 96 638809734
game_id in gotten_game_ids
7013 # 96 638290589
game_id in gotten_game_ids
7013 # 96 1144395230
game_id in gotten_game_ids
7013 # 96 1507663490
game_id in gotten_game_ids
7013 # 96 722000616
game_id in gotten_game_ids
7013 # 96 739117893
game_id in gotten_game_ids
7013 # 96 13555841

7013 # 97 1191251781
game_id in gotten_game_ids
7013 # 97 1233033818
game_id in gotten_game_ids
7013 # 97 1064459184
game_id in gotten_game_ids
7013 # 97 1457956575
game_id in gotten_game_ids
7013 # 97 1219962482
game_id in gotten_game_ids
7013 # 97 1061861560
game_id in gotten_game_ids
7013 # 97 1383234801
game_id in gotten_game_ids
7013 # 97 704484890
game_id in gotten_game_ids
7013 # 97 1399253988
game_id in gotten_game_ids
7013 # 97 1137573314
game_id in gotten_game_ids
7013 # 97 1435850686
game_id in gotten_game_ids
7013 # 97 1191353970
game_id in gotten_game_ids
7013 # 97 1037758394
game_id in gotten_game_ids
7013 # 97 982249933
game_id in gotten_game_ids
7013 # 97 966549025
game_id in gotten_game_ids
7013 # 97 684265507
game_id in gotten_game_ids
7013 # 97 967288662
game_id in gotten_game_ids
7013 # 97 718360161
game_id in gotten_game_ids
7013 # 97 1481356528
game_id in gotten_game_ids
7013 # 97 1501503932
game_id in gotten_game_ids
7013 # 97 1348706111
game_id in gotten_game_id

game_id in gotten_game_ids
7013 # 98 1247758515
game_id in gotten_game_ids
7013 # 98 1174914156
game_id in gotten_game_ids
7013 # 98 1035248125
game_id in gotten_game_ids
7013 # 98 1343820018
game_id in gotten_game_ids
7013 # 98 1120448984
game_id in gotten_game_ids
7013 # 98 1369072543
game_id in gotten_game_ids
7013 # 98 680324411
game_id in gotten_game_ids
7013 # 98 1078019201
game_id in gotten_game_ids
7013 # 98 1012288691
game_id in gotten_game_ids
7013 # 98 1097480526
game_id in gotten_game_ids
7013 # 98 1363224875
game_id in gotten_game_ids
7013 # 98 1080602764
game_id in gotten_game_ids
7013 # 98 1235159369
game_id in gotten_game_ids
7013 # 98 1515691347
game_id in gotten_game_ids
7013 # 98 383026661
game_id in gotten_game_ids
7013 # 98 1001425491
game_id in gotten_game_ids
7013 # 98 1106279439
game_id in gotten_game_ids
7013 # 98 1374868881
game_id in gotten_game_ids
7013 # 98 1037985078
game_id in gotten_game_ids
7013 # 98 1160747981
game_id in gotten_game_ids
7013 # 98 13346

game_id in gotten_game_ids
7013 # 99 1215477266
game_id in gotten_game_ids
7013 # 99 1469018846
game_id in gotten_game_ids
7013 # 99 1339799311
game_id in gotten_game_ids
7013 # 99 1269013920
game_id in gotten_game_ids
7013 # 99 883393043
game_id in gotten_game_ids
7013 # 99 1258728201
game_id in gotten_game_ids
7013 # 99 1315942961
game_id in gotten_game_ids
7013 # 99 510461758
game_id in gotten_game_ids
7013 # 99 1151786843
game_id in gotten_game_ids
7013 # 99 1448878746
game_id in gotten_game_ids
7013 # 99 1252723077
game_id in gotten_game_ids
7013 # 99 1030414975
game_id in gotten_game_ids
7013 # 99 1140390871
game_id in gotten_game_ids
7013 # 99 728648804
game_id in gotten_game_ids
7013 # 99 1440293350
game_id in gotten_game_ids
7013 # 99 1209177598
game_id in gotten_game_ids
7013 # 99 1089119435
game_id in gotten_game_ids
7013 # 99 1184934001
game_id in gotten_game_ids
7013 # 99 322656719
game_id in gotten_game_ids
7013 # 99 1002773110
game_id in gotten_game_ids
7013 # 99 9717565

In [ ]:
len(gotten_game_ids)

##### multi process

import multiprocessing as multi
n_cores = multi.cpu_count()
n_cores

def main(sub_genre_id):
    i = 0
    for letter in letters:
        for page in pages:
            i += 1
            print(i, sub_genre_id, letter, page)
            url = url_parent.format(sub_genre_id, letter, page)
            game_ids = get_game_id(url)
            if len(game_ids) == 0:
                print('hoge')
                break
            for game_id in game_ids:
                write_json_file(game_id)

%%time
n_cores = multi.cpu_count()
sub_genre_ids = list(sub_genre_id_dict.values())
with Pool(processes=n_cores) as p:
    p.map(func=main, iterable=sub_genre_ids)